In [1]:
%config Completer.use_jedi = False
import warnings
warnings.filterwarnings(action="ignore")
import numpy as np
import pandas as pd
import requests
import json
import folium
from pandas.io.json import json_normalize


In [2]:
# 따릉이 서버에 post 방식으로 요청해서 서버가 응답하는 데이터를 받는다.
targetSite = 'https://www.bikeseoul.com/app/station/getStationRealtimeStatus.do'
request = requests.post(targetSite, data = {
    'stationGrpSeq' : 'ALL'
})
#print(request)
#print(type(request.text))
#print(request.text)

In [3]:
# 따릉이 서버가 응답하는 json 형태의 문자열을 파이썬에서 사용하기 위해 
# 딕셔너리 형태로 변환한다.
#bike_json = json.loads(request.text) # json 모듈의 loads() 메소드 사용
bike_json = request.json()
print(type(bike_json))
print(bike_json.keys())

<class 'dict'>
dict_keys(['stationImgPath', 'appUserSessionVO', 'loginYn', 'realtimeList', 'sessionId', 'stationVO', 'checkResult'])


In [4]:
#bike_json['realtimeList']
bike_json.get('realtimeList')

[{'stationName': '102. 망원역 1번출구 앞',
  'stationImgFileName': '',
  'stationId': 'ST-4',
  'stationLongitude': '126.91062927',
  'stationLatitude': '37.55564880',
  'rackTotCnt': '15',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '10',
  'parkingELECBikeCnt': '4',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationName': '103. 망원역 2번출구 앞',
  'stationImgFileName': '',
  'stationId': 'ST-5',
  'stationLongitude': '126.91083527',
  'stationLatitude': '37.55495071',
  'rackTotCnt': '14',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '4',
  'parkingELECBikeCnt': '4',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationName': '104. 합정역 1번출구 앞',
  'stationImgFileName': '',
  'stationId': 'ST-6',
  'stationLongitude': '126.91508484',
  'stationLatitude': '37.55073929',
  'rackTotCnt': '13',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '0',
  'parkingELECBikeCnt': '2',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationName': '105. 합정역 5번출구 앞',
  'stationImgFileName': '',

In [5]:
# pandas.io.json 모듈의 json_normalize() 메소드로 json 타입의 데이터가 변환된 딕셔너리를
# 데이터프레임으로 변환한다. 
# json_normalize (딕셔너리, 데이터프레임으로 변환할 데이터가 할당된 딕셔너리의 key)
bicycle_df = pd.json_normalize(bike_json, 'realtimeList')
bicycle_df

stationName stationImgFileName stationId stationLongitude  \
0       102. 망원역 1번출구 앞                         ST-4     126.91062927   
1       103. 망원역 2번출구 앞                         ST-5     126.91083527   
2       104. 합정역 1번출구 앞                         ST-6     126.91508484   
3       105. 합정역 5번출구 앞                         ST-7     126.91482544   
4       106. 합정역 7번출구 앞                         ST-8     126.91282654   
...                 ...                ...       ...              ...   
2723  6058. 서울도시건축전시관 옆                      ST-3297     126.97684479   
2724  6058. 서울도시건축전시관 옆                      ST-3297     126.97684479   
2725       6171. 월드빌딩 앞                      ST-3276     126.83743286   
2726     6172. 가양5단지아파트                      ST-3281     126.85464478   
2727  6173. 서울자동차운전전문학원                      ST-3284     126.82106018   

     stationLatitude rackTotCnt parkingBikeTotCnt parkingQRBikeCnt  \
0        37.55564880         15                 0               10   
1        37.55495071         14                 0                4   
2        37.55073929         13                 0                0   
3        37.55000687          5                 0                1   
4        37.54864502         12                 0                0   
...              ...        ...               ...              ...   
2723     37.56653976         10                 0                1   
2724     37.56653976         10                 0                1   
2725     37.54098129         12                 0               22   
2726     37.56447983         10                 0                0   
2727     37.54613495         10                 0               19   

     parkingELECBikeCnt stationSeCd  mode  
0                     4     RAK_002  None  
1                     4     RAK_002  None  
2                     2     RAK_002  None  
3                     0     RAK_002  None  
4                     0     RAK_002  None  
...                 ...         ...   ...  
2723                  0     RAK_002  None  
2724                  0     RAK_002  None  
2725                  0     RAK_002  None  
2726                  0     RAK_002  None  
2727                  0     RAK_002  None  

[2728 rows x 11 columns]

In [6]:
bicycle_df.columns

Index(['stationName', 'stationImgFileName', 'stationId', 'stationLongitude',
       'stationLatitude', 'rackTotCnt', 'parkingBikeTotCnt',
       'parkingQRBikeCnt', 'parkingELECBikeCnt', 'stationSeCd', 'mode'],
      dtype='object')

In [7]:
# stationId : 대여소 id
# stationName : 대여소 이름
# parkingBikeTotCnt : 주차된 따릉이 lcd형 댓수 -> 사용하지 않음
# parkingQRBikeCnt : 주차된 따릉이 QR형 댓수 -> 일반 따릉이
# parkingELECBikeCnt : 주차된 새싹 따릉이 댓수
# stationLongitude : 대여소 경도
# stationLatitude : 대여소 위도
# rackTotCnt : 주차 가능한 자전거 댓수

In [8]:
bicycle_df_refined = bicycle_df[['stationId',
                                 'stationName',
                                 'parkingQRBikeCnt',
                                 'parkingELECBikeCnt',
                                 'stationLatitude',
                                 'stationLongitude',
                                ]]
bicycle_df_refined 

stationId        stationName parkingQRBikeCnt parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞               10                  4   
1         ST-5    103. 망원역 2번출구 앞                4                  4   
2         ST-6    104. 합정역 1번출구 앞                0                  2   
3         ST-7    105. 합정역 5번출구 앞                1                  0   
4         ST-8    106. 합정역 7번출구 앞                0                  0   
...        ...                ...              ...                ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                1                  0   
2724   ST-3297  6058. 서울도시건축전시관 옆                1                  0   
2725   ST-3276       6171. 월드빌딩 앞               22                  0   
2726   ST-3281     6172. 가양5단지아파트                0                  0   
2727   ST-3284  6173. 서울자동차운전전문학원               19                  0   

     stationLatitude stationLongitude  
0        37.55564880     126.91062927  
1        37.55495071     126.91083527  
2        37.55073929     126.91508484  
3        37.55000687     126.91482544  
4        37.54864502     126.91282654  
...              ...              ...  
2723     37.56653976     126.97684479  
2724     37.56653976     126.97684479  
2725     37.54098129     126.83743286  
2726     37.56447983     126.85464478  
2727     37.54613495     126.82106018  

[2728 rows x 6 columns]

In [9]:
#bicycle_df_refined.dtypes
bicycle_df_refined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2728 entries, 0 to 2727
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   stationId           2728 non-null   object
 1   stationName         2728 non-null   object
 2   parkingQRBikeCnt    2728 non-null   object
 3   parkingELECBikeCnt  2728 non-null   object
 4   stationLatitude     2728 non-null   object
 5   stationLongitude    2728 non-null   object
dtypes: object(6)
memory usage: 128.0+ KB


In [10]:
bicycle_df_refined['parkingQRBikeCnt'] = bicycle_df_refined.parkingQRBikeCnt.astype(int)
bicycle_df_refined['parkingELECBikeCnt'] = bicycle_df_refined.parkingELECBikeCnt.astype('int')
bicycle_df_refined['stationLatitude'] = bicycle_df_refined.stationLatitude.astype(float)
bicycle_df_refined['stationLongitude'] = bicycle_df_refined.stationLongitude.astype('float')
bicycle_df_refined['parking_total'] = ( bicycle_df_refined.parkingQRBikeCnt + 
                                          bicycle_df_refined.parkingELECBikeCnt )
bicycle_df_refined

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                10                   4   
1         ST-5    103. 망원역 2번출구 앞                 4                   4   
2         ST-6    104. 합정역 1번출구 앞                 0                   2   
3         ST-7    105. 합정역 5번출구 앞                 1                   0   
4         ST-8    106. 합정역 7번출구 앞                 0                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2725   ST-3276       6171. 월드빌딩 앞                22                   0   
2726   ST-3281     6172. 가양5단지아파트                 0                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                19                   0   

      stationLatitude  stationLongitude  parking_total  
0           37.555649        126.910629             14  
1           37.554951        126.910835              8  
2           37.550739        126.915085              2  
3           37.550007        126.914825              1  
4           37.548645        126.912827              0  
...               ...               ...            ...  
2723        37.566540        126.976845              1  
2724        37.566540        126.976845              1  
2725        37.540981        126.837433             22  
2726        37.564480        126.854645              0  
2727        37.546135        126.821060             19  

[2728 rows x 7 columns]

In [11]:
bicycle_df_refined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2728 entries, 0 to 2727
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   stationId           2728 non-null   object 
 1   stationName         2728 non-null   object 
 2   parkingQRBikeCnt    2728 non-null   int32  
 3   parkingELECBikeCnt  2728 non-null   int32  
 4   stationLatitude     2728 non-null   float64
 5   stationLongitude    2728 non-null   float64
 6   parking_total       2728 non-null   int32  
dtypes: float64(2), int32(3), object(2)
memory usage: 117.3+ KB


In [12]:
bicycle_df_refined.to_csv('./data/bicycle_df_refined.csv', index=False)

***
Geo Coding
***
지오코딩 -> 주소로 위도, 경도 얻기, 역지오코딩 -> 위도, 경도로 주소 얻기  
pip install geopy 
  
 GeocoderUnavailable: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /search?q=%EC%84%9C%EC%9A%B8%EC%8B%9C+%EC%A2%85%EB%A1%9C%EA%B5%AC+%EA%B4%80%EC%B2%A0%EB%8F%99&format=json&limit=1 (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: certificate has expired (_ssl.c:1091)')))  
 위와 같은 에러가 발생되면 아래의 코드를 추가하고 실행한다.  
   
   
 import certifi
import ssl
import geopy.geocoders  

ctx = ssl.create_default_context(cafile=certifi.where())
geopy.geocoders.options.default_ssl_context = ctx

In [13]:
from geopy.geocoders import Nominatim

In [14]:
# 지오코딩 함수 -> 주소를 인수로 넘겨받아 위도, 경도를 리턴하는 함수
def geoCoding(address):
    geocoder = Nominatim(user_agent='South Korea', timeout=None)
    geo = geocoder.geocode(address)
    return {'위도' : geo.latitude, '경도' : geo.longitude}

In [15]:
'''
address = geoCoding('서울시 종로구 관철동')
print(address)
address = geoCoding('경기도 양주시 양주2동')
print(address)
'''
pass

In [16]:
# 역지오코딩 함수 ->  위도, 경도를 넘겨받아 주소를 리턴하는 함수
def geoCodingReverse(lat_lot):
    geocoder = Nominatim(user_agent='South Korea', timeout=None)
    return geocoder.reverse(lat_lot)

In [17]:
'''
#address = geoCodingReverse( (37.796081799999996,127.10584381013413) )
address = geoCodingReverse( ' 37.796081799999996, 127.10584381013413 ' )
#print(address)
#print(type(address))
addr = str(address).split(', ')
# ['양주2동 주민자치센터', '삼숭로38번길', '삼숭동', '양주시', '11484', '대한민국']
print(addr[-3], addr[-4], addr[-5])
#print(type(addr))

address = geoCodingReverse( ' 37.570697576083994, 126.98824455071323 ' )
addr = str(address).split(', ')
#['탑골공원', '99', '종로', '종로3가', '종로1·2·3·4가동', '종로구', '서울특별시', '03140', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geoCodingReverse( ' 35.1588864538351, 129.1594966810267 ' )
addr = str(address).split(', ')
#['해운대 해수욕장', '해운대해변로209번길', '우1동', '해운대구', '부산광역시', '48093', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geoCodingReverse( ' 36.771309432752226, 128.07408756806268 ' )
addr = str(address).split(', ')
#['문경세제오픈세트장', '문경새재 오픈세트장', '문경시', '경상북도', '36919', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geoCodingReverse( '37.555649,	126.910629 ' )
addr = str(address).split(', ')
#['스타벅스', '74', '월드컵로', '서교동', '마포구', '서울특별시', '04004', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geoCodingReverse( '37.546135 	126.821060 ' )
addr = str(address).split(', ')
#['222', '남부순환로', '외발산동', '발산1동', '강서구', '서울특별시', '07506', '대한민국']
print(addr[-3], addr[-4], addr[-5])
'''
pass

In [18]:
bicycle_df_refined['gu'] = np.NaN
bicycle_df_refined['dong'] = np.NaN
bicycle_df_refined

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                10                   4   
1         ST-5    103. 망원역 2번출구 앞                 4                   4   
2         ST-6    104. 합정역 1번출구 앞                 0                   2   
3         ST-7    105. 합정역 5번출구 앞                 1                   0   
4         ST-8    106. 합정역 7번출구 앞                 0                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2725   ST-3276       6171. 월드빌딩 앞                22                   0   
2726   ST-3281     6172. 가양5단지아파트                 0                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                19                   0   

      stationLatitude  stationLongitude  parking_total  gu  dong  
0           37.555649        126.910629             14 NaN   NaN  
1           37.554951        126.910835              8 NaN   NaN  
2           37.550739        126.915085              2 NaN   NaN  
3           37.550007        126.914825              1 NaN   NaN  
4           37.548645        126.912827              0 NaN   NaN  
...               ...               ...            ...  ..   ...  
2723        37.566540        126.976845              1 NaN   NaN  
2724        37.566540        126.976845              1 NaN   NaN  
2725        37.540981        126.837433             22 NaN   NaN  
2726        37.564480        126.854645              0 NaN   NaN  
2727        37.546135        126.821060             19 NaN   NaN  

[2728 rows x 9 columns]

In [19]:
'''
for i in range(bicycle_df_refined.shape[0])[:]:
    lat_lot = '{}, {}'.format(bicycle_df_refined.loc[i, 'stationLatitude'],
                              bicycle_df_refined.loc[i, 'stationLongitude'])
    #print(lat_lot)
    address = geoCodingReverse(lat_lot)
    addr = str(address).split(', ')
    #print(i, addr[-4], addr[-5])
    try:
        bicycle_df_refined.loc[i, 'gu'] = addr[-4]
    except:
        print( '{}번째 인덱스 스테이션 -4번째 주소 없음'.format(i) )
    
    try:
        bicycle_df_refined.loc[i, 'dong'] = addr[-5]
    except:
        print( '{}번째 인덱스 스테이션 -5번째 주소 없음'.format(i) )
    if (i + 1) % 20 == 0:
        print('--------', (i + 1), '--------')
    
bicycle_df_refined
'''
pass

In [20]:
#bicycle_df_refined.to_csv('./data/ttareungyi.csv', index=False)

In [21]:
bicycle_df_refined = pd.read_csv('./data/ttareungyi.csv')


In [22]:
bicycle_df_refined[bicycle_df_refined.gu.isnull() | bicycle_df_refined.dong.isna()]

stationId          stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
44      ST-212      155. 가좌역1 번출구 앞                 0                   4   
64      ST-232      179. 가좌역 4번출구 앞                 3                  15   
1356   ST-2352      2079.중앙대학교 중앙광장                 3                   3   
2097   ST-3225  3934. 철도교통관제센터 정문 앞                10                   0   
2532   ST-3024   4837. 양원지구 힐데스하임 앞                15                   1   

      stationLatitude  stationLongitude  parking_total     gu dong  
44          37.568295        126.915047              4   성산2동  NaN  
64          37.568775        126.915298             18  남가좌1동  NaN  
1356        37.506672        126.957779              6    흑석동  NaN  
2097        37.497082        126.877884             10   구로1동  NaN  
2532        37.609241        127.106209             16   망우본동  NaN

In [23]:
bicycle_df_refined[bicycle_df_refined.gu.isnull() | bicycle_df_refined.dong.isna()].stationId

44       ST-212
64       ST-232
1356    ST-2352
2097    ST-3225
2532    ST-3024
Name: stationId, dtype: object

In [24]:
errorList = list(bicycle_df_refined[bicycle_df_refined.gu.isnull() | bicycle_df_refined.dong.isna()].stationId)
print(errorList)
print(type(errorList))

['ST-212', 'ST-232', 'ST-2352', 'ST-3225', 'ST-3024']
<class 'list'>


In [31]:
for error in errorList:
    bicycle_error = bicycle_df_refined[bicycle_df_refined.stationId == error]
    #print(bicycle_error)
    print('-'*100)
    lat_lot = '{}, {}'.format( bicycle_error.iloc[0, 4], #경도
                              bicycle_error.iloc[0, 5] ) #위도
    #print(lat_lot)
    print(bicycle_error.index)
    #print( bicycle_df_refined.loc[bicycle_error.index, 'gu'] )
    #lat_lot2 = '{}, {}'.format(bicycle_error.loc[bicycle_error.index[0], 'stationLatitude'],
    #                          bicycle_error.loc[bicycle_error.index[0], 'stationLongitude'])
    address = geoCodingReverse(lat_lot)
    addr = str(address).split(', ')
    bicycle_df_refined.loc[bicycle_error.index, 'gu'] = addr[-3]
    bicycle_df_refined.loc[bicycle_error.index, 'dong'] = addr[-4]
    
bicycle_df_refined[bicycle_df_refined.gu.isnull() | bicycle_df_refined.dong.isna()]

----------------------------------------------------------------------------------------------------
Int64Index([44], dtype='int64')
----------------------------------------------------------------------------------------------------
Int64Index([64], dtype='int64')
----------------------------------------------------------------------------------------------------
Int64Index([1356], dtype='int64')
----------------------------------------------------------------------------------------------------
Int64Index([2097], dtype='int64')
----------------------------------------------------------------------------------------------------
Int64Index([2532], dtype='int64')


Empty DataFrame
Columns: [stationId, stationName, parkingQRBikeCnt, parkingELECBikeCnt, stationLatitude, stationLongitude, parking_total, gu, dong]
Index: []

In [26]:
bicycle_df_refined

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                 0                   2   
1         ST-5    103. 망원역 2번출구 앞                 1                   3   
2         ST-6    104. 합정역 1번출구 앞                23                   2   
3         ST-7    105. 합정역 5번출구 앞                 2                   1   
4         ST-8    106. 합정역 7번출구 앞                 1                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 2                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 2                   0   
2725   ST-3276       6171. 월드빌딩 앞                21                   0   
2726   ST-3281     6172. 가양5단지아파트                 1                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                19                   0   

      stationLatitude  stationLongitude  parking_total   gu  dong  
0           37.555649        126.910629              2  마포구   서교동  
1           37.554951        126.910835              4  마포구  망원1동  
2           37.550739        126.915085             25  마포구   서교동  
3           37.550007        126.914825              3  마포구   서교동  
4           37.548645        126.912827              1  마포구   합정동  
...               ...               ...            ...  ...   ...  
2723        37.566540        126.976845              2   중구   소공동  
2724        37.566540        126.976845              2   중구   소공동  
2725        37.540981        126.837433             21  강서구  화곡1동  
2726        37.564480        126.854645              1  강서구  가양2동  
2727        37.546135        126.821060             19  강서구  발산1동  

[2728 rows x 9 columns]

In [27]:
#bicycle_df_refined.to_csv('./data/ttareungyi_ok.csv', index=False)
bicycle_df_refined_ok = pd.read_csv('./data/ttareungyi_ok.csv')
bicycle_df_refined_ok

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                 0                   2   
1         ST-5    103. 망원역 2번출구 앞                 1                   3   
2         ST-6    104. 합정역 1번출구 앞                23                   2   
3         ST-7    105. 합정역 5번출구 앞                 2                   1   
4         ST-8    106. 합정역 7번출구 앞                 1                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 2                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 2                   0   
2725   ST-3276       6171. 월드빌딩 앞                21                   0   
2726   ST-3281     6172. 가양5단지아파트                 1                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                19                   0   

      stationLatitude  stationLongitude  parking_total   gu  dong  
0           37.555649        126.910629              2  마포구   서교동  
1           37.554951        126.910835              4  마포구  망원1동  
2           37.550739        126.915085             25  마포구   서교동  
3           37.550007        126.914825              3  마포구   서교동  
4           37.548645        126.912827              1  마포구   합정동  
...               ...               ...            ...  ...   ...  
2723        37.566540        126.976845              2   중구   소공동  
2724        37.566540        126.976845              2   중구   소공동  
2725        37.540981        126.837433             21  강서구  화곡1동  
2726        37.564480        126.854645              1  강서구  가양2동  
2727        37.546135        126.821060             19  강서구  발산1동  

[2728 rows x 9 columns]

***
서울시 따릉이 스테이션 위치 시각화
***

In [28]:
bicycle = bicycle_df_refined_ok
bicycle_map_seoul = folium.Map(location=[bicycle.stationLatitude.mean(), bicycle.stationLongitude.mean()], zoom_start=12)
for index, data in bicycle.iterrows():
    
    station = data.stationName.split('.')
    '''
    if len(station) == 1:
        stationName = station[0]
    else :
        stationName = station[1]
    '''
    stationName = station[0] if len(station) == 1 else station[1]
    string = '{} -> 일반: {}대, 새싹 : {}'.format(data.stationName.strip(),
                                                data.parkingQRBikeCnt,
                                                 data.parkingELECBikeCnt)
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker(location=[data.stationLatitude, data.stationLongitude], popup=stationInfo, icon=folium.Icon(color='darkred', icon='ok')).add_to(bicycle_map_seoul)

bicycle_map_seoul.save('./output/bicycle_map_seoul.html')
bicycle_map_seoul

***
종로구 따릉이 스테이션 위치 시각화
***

In [29]:
bicycle = bicycle_df_refined_ok[bicycle_df_refined_ok.gu.str.find('종로') != -1]
bicycle_map_seoul = folium.Map(location=[bicycle.stationLatitude.mean(), bicycle.stationLongitude.mean()], zoom_start=12)
for index, data in bicycle.iterrows():
    
    station = data.stationName.split('.')
    '''
    if len(station) == 1:
        stationName = station[0]
    else :
        stationName = station[1]
    '''
    stationName = station[0] if len(station) == 1 else station[1]
    string = '{} -> 일반: {}대, 새싹 : {}'.format(data.stationName.strip(),
                                                data.parkingQRBikeCnt,
                                                 data.parkingELECBikeCnt)
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker(location=[data.stationLatitude, data.stationLongitude], popup=stationInfo, icon=folium.Icon(color='green', icon='ok')).add_to(bicycle_map_seoul)

bicycle_map_seoul.save('./output/bicycle_map_seoul.html')
bicycle_map_seoul